# Comparison of the assay and hyperspectral datas

The assay file contains the `Hole_ID` of every drillhole, their position in the hole, the chemical composition of the sample (Fe, Fe2O3, P, S, SiO2, Al2O3, MnO, Mn, CaO, K2O, MgO, Na2O, TiO2) and the loss-on-ignition percentage.
The hyperspectral file contains the `Hole_ID` of every drillhole, their position in the hole, the chemical composition of each sample (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn), the loss-on-ignition percentage and other informations about the minerals in the sample.

The common data between these two files are the `Hole_ID`, the depth, most columns about chemical composition (Fe, Al2O3, SiO2, K2O, CaO, MgO, TiO2, P, S, Mn) and the loss-on-ignition percentage.

The aim of this notebook is to compare the two files in order to find the common holes and compare the values in identical holes in order to assess lab results from the two different techniques beign hyperspectral and XRF.

In [ ]:
import numpy as np
import pandas as pd
import geolime as geo
import seaborn as sns

Format Pandas display for clarity and readability

In [ ]:
pd.set_option("display.max_rows", 10)
pd.set_option("display.max_columns", 500)

We want to compare the `Hole_ID` of the assay and hyperspectral file to know if they have some drillholes in common.

First we need to import these data from `.csv` files.

## Merging Interval Files 

### Assay File reading and formatting

In [ ]:
assay = geo.datasets.load("rocklea_dome/assay.csv")
assay

Some columns have string values named LNR, replacing them to NaN will allow comparisons with other number columns. Using the `.dtypes` information allows to find out wich columns are considered numerical (float64 or int64) and which column are considered as string/text and are identified by Pandas as object.

In [ ]:
assay.dtypes

Using the `eq` method makes it easy to find if any column has a value equals to "LNR".

In [ ]:
assay.eq("LNR").any()

Replacing the problematic value by nan (which means 'not a number' but is considered as a numeric information by Pandas and Numpy) and then making sure the column are converted into numeric values is done in two step.

In [ ]:
assay.replace("LNR", np.nan, inplace=True)
assay[["P", "S", "TiO2", "LOI"]] = assay[["P", "S", "TiO2", "LOI"]].apply(pd.to_numeric)

### Hyperspec File reading

In [ ]:
hyperspec = pd.read_csv("../data/hyperspec.csv")
hyperspec

### Merge Preparation

The comparison of the two datasets require to have the list of the different `Hole_ID` of both files. These lists also need to be turned into sets in order to compare them.
The set type ensures there are no duplicate values, being useful here as `Hole_ID` are unique identifier.

In [ ]:
colonne_assay = set(assay["Hole_ID"])
colonne_hyperspec = set(hyperspec["Hole_ID"])

Now we have two sets with the different drill core that have been analyzed for each method. 

The length of each set indicates how many holes are present in each dataset.

In [ ]:
len(colonne_assay)

In [ ]:
len(colonne_hyperspec)

The two file do not have the same amount of hole. The set type enables ensemble query such as intersection/union/difference. The intersection here will allow to find the common hole between the two dataset.

Next command will search all the `Hole_ID` both in the assay and hyperspec file.

In [ ]:
intersection = colonne_assay.intersection(colonne_hyperspec)

In [ ]:
len(intersection)

The intersection of these two files has the same length as the smallest set, so every `Hole_ID` of the hyperspectral file are in the assay.

The drill cores of the hyperspectral file are included in the assay file. Now we want to see if the common columns between these two files have the same values. First we need to filter the DataFrame of the assay file in order to keep only the `Hole_ID` that are in common with the hyperspectral file.

In [ ]:
intersection = list(intersection)
filtred_assay = assay[assay["Hole_ID"].isin(intersection)]
filtred_assay

The next operation will delete every sample of the assay file that is not in the hyperspectral file and make sure that we have the exact same number of `Hole_ID` in both files.

In [ ]:
assay_final = hyperspec.merge(filtred_assay, on=["Hole_ID", "From", "To"], how="left")
assay_final.sort_values(by=["Hole_ID", "From"], inplace=True)
assay_final

### Merged Data Verification

This new file allows to make comparison between the data from the assay file (obtain by a XRF analysis) and the data from the hyperspectral analysis.

First we can compare the Fe weight percentage :

In [ ]:
sns.scatterplot(data=assay_final, x="Fe", y="Fe_pct");

Most of the measures are similar for both methods. We can do the same for the Al2O3 weight percentage :

In [ ]:
sns.scatterplot(data=assay_final, x="Al2O3_x", y="Al2O3_y");

In [ ]:
assay_final.drop(columns=["Al2O3_y", "LOI_x", "LOI_y"], inplace=True)
assay_final.rename(columns={"Al2O3_x": "Al2O3"}, inplace=True)

In [ ]:
assay_final.to_csv("../data/assay_hyper.csv", index=False)